In [1]:
# Install necessary packages
!pip install opencv-python numpy matplotlib scipy open3d


[notice] A new release of pip is available: 25.0.1 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import os
import numpy as np
import cv2
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import open3d as o3d
import glob
from scipy.spatial.transform import Rotation as R

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [3]:
# Set the path to your data
data_path = 'temple'

# Read camera parameters from temple_par.txt
par_path = os.path.join(data_path, 'temple_par.txt')
params = []
with open(par_path, 'r') as f:
    lines = f.readlines()
    # Skip the first line if it contains just the number of images
    start_idx = 1 if lines[0].strip().isdigit() else 0
    for line in lines[start_idx:]:
        parts = line.strip().split()
        if len(parts) > 21:  # Ensure it has all parameters
            img_name = parts[0]
            # K matrix (intrinsic parameters)
            K = np.array([
                [float(parts[1]), float(parts[2]), float(parts[3])],
                [float(parts[4]), float(parts[5]), float(parts[6])],
                [float(parts[7]), float(parts[8]), float(parts[9])]
            ])
            # R matrix (rotation)
            R_mat = np.array([
                [float(parts[10]), float(parts[11]), float(parts[12])],
                [float(parts[13]), float(parts[14]), float(parts[15])],
                [float(parts[16]), float(parts[17]), float(parts[18])]
            ])
            # t vector (translation)
            t = np.array([float(parts[19]), float(parts[20]), float(parts[21])])

            params.append({
                'img_name': img_name,
                'K': K,
                'R': R_mat,
                't': t
            })

print(f"Loaded parameters for {len(params)} images")

# Read angle information from temple_ang.txt
ang_path = os.path.join(data_path, 'temple_ang.txt')
angles = {}
with open(ang_path, 'r') as f:
    for line in f:
        parts = line.strip().split()
        if len(parts) >= 3:
            lat, lon, img_name = float(parts[0]), float(parts[1]), parts[2]
            angles[img_name] = (lat, lon)

print(f"Loaded angles for {len(angles)} images")

Loaded parameters for 312 images
Loaded angles for 312 images


In [4]:
# Print a sample of the loaded parameters
if params:
    print("\nSample camera parameters:")
    sample = params[0]
    print(f"Image name: {sample['img_name']}")
    print(f"Intrinsic matrix K:\n{sample['K']}")
    print(f"Rotation matrix R:\n{sample['R']}")
    print(f"Translation vector t:\n{sample['t']}")

# Print a sample of the loaded angles
if angles:
    print("\nSample angle information:")
    sample_key = next(iter(angles))
    lat, lon = angles[sample_key]
    print(f"Image name: {sample_key}")
    print(f"Latitude: {lat}, Longitude: {lon}")


Sample camera parameters:
Image name: temple0001.png
Intrinsic matrix K:
[[1.5204e+03 0.0000e+00 3.0232e+02]
 [0.0000e+00 1.5259e+03 2.4687e+02]
 [0.0000e+00 0.0000e+00 1.0000e+00]]
Rotation matrix R:
[[ 0.01551372  0.99884344 -0.04550951]
 [ 0.99922239 -0.0171375  -0.03550953]
 [-0.03624838 -0.04492323 -0.99833259]]
Translation vector t:
[-0.05998548  0.00400788  0.57088647]

Sample angle information:
Image name: temple0001.png
Latitude: -90.0, Longitude: 185.0


In [13]:
import plotly.subplots as sp
import plotly.graph_objects as go
import numpy as np
import cv2
import os

# Load and display images using Plotly
image_files = sorted([f for f in os.listdir(data_path) if f.endswith('.png')])[0:9:2]  # First 5 images

# Create subplot figure
fig = sp.make_subplots(rows=1, cols=5, 
                      subplot_titles=image_files,
                      specs=[[{'type': 'image'} for _ in range(5)]])

for i, img_file in enumerate(image_files):
    img_path = os.path.join(data_path, img_file)
    img = cv2.imread(img_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    
    # Add image to subplot
    fig.add_trace(
        go.Image(z=img),
        row=1, col=i+1
    )

# Update layout
fig.update_layout(
    title_text="Temple Dataset Sample Images",
    height=500,
    width=1200,
    showlegend=False,
)

# Remove axes
fig.update_xaxes(showticklabels=False, showgrid=False, zeroline=False)
fig.update_yaxes(showticklabels=False, showgrid=False, zeroline=False)

fig.show()

In [7]:
import plotly.graph_objects as go
import numpy as np

def plot_cameras_plotly(params):
    # Create a new 3D figure
    fig = go.Figure()
    
    # Extract camera centers and orientations
    camera_centers = []
    for i, param in enumerate(params):
        R_mat = param['R']
        t = param['t']

        # Camera center in world coordinates: C = -R^T * t
        C = -np.dot(R_mat.T, t)
        camera_centers.append(C)
        
        # Add camera center as a marker
        fig.add_trace(go.Scatter3d(
            x=[C[0]], 
            y=[C[1]], 
            z=[C[2]],
            mode='markers',
            marker=dict(
                size=5,
                color='blue',
            ),
            name=f'Camera {i+1}'
        ))
        
        # Plot camera direction (optical axis)
        # The third column of R gives the direction of the z-axis
        direction = R_mat[:, 2]
        arrow_length = 0.05
        
        # Add camera direction as an arrow
        fig.add_trace(go.Scatter3d(
            x=[C[0], C[0] + arrow_length * direction[0]],
            y=[C[1], C[1] + arrow_length * direction[1]],
            z=[C[2], C[2] + arrow_length * direction[2]],
            mode='lines',
            line=dict(color='red', width=3),
            showlegend=False
        ))

    camera_centers = np.array(camera_centers)
    
    # Set layout with equal aspect ratio
    max_range = np.array([
        camera_centers[:, 0].max() - camera_centers[:, 0].min(),
        camera_centers[:, 1].max() - camera_centers[:, 1].min(),
        camera_centers[:, 2].max() - camera_centers[:, 2].min()
    ]).max() / 2.0

    mid_x = (camera_centers[:, 0].max() + camera_centers[:, 0].min()) * 0.5
    mid_y = (camera_centers[:, 1].max() + camera_centers[:, 1].min()) * 0.5
    mid_z = (camera_centers[:, 2].max() + camera_centers[:, 2].min()) * 0.5
    
    # Configure the layout for better visualization
    fig.update_layout(
        title='Camera Positions and Orientations',
        scene=dict(
            xaxis=dict(
                range=[mid_x - max_range, mid_x + max_range],
                title='X'
            ),
            yaxis=dict(
                range=[mid_y - max_range, mid_y + max_range],
                title='Y'
            ),
            zaxis=dict(
                range=[mid_z - max_range, mid_z + max_range],
                title='Z'
            ),
            aspectmode='cube'
        ),
        margin=dict(l=0, r=0, b=0, t=40),
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01
        )
    )
    
    return fig

# Example usage:
fig = plot_cameras_plotly(params)
fig.show()

In [ ]:
import numpy as np
import cv2
import open3d as o3d
import os
import random
import copy
from tqdm import tqdm

def load_camera_angles(angle_file_path):
    """
    Load camera angles from temple_ang.txt file.
    """
    camera_angles = {}
    try:
        with open(angle_file_path, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if len(parts) == 3:
                    # Format: elevation azimuth filename
                    elevation = float(parts[0])
                    azimuth = float(parts[1])
                    img_name = parts[2]
                    camera_angles[img_name] = {
                        'elevation': elevation,
                        'azimuth': azimuth
                    }
    except Exception as e:
        print(f"Error loading camera angles: {e}")
    
    return camera_angles

def detect_and_compute_features(img_path):
    """
    Detect and compute SIFT features for an image.
    """
    img = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)
    if img is None:
        print(f"Error loading image: {img_path}")
        return None, [], None
        
    # Use SIFT with even more features and better parameters for ultra-dense reconstruction
    sift = cv2.SIFT_create(nfeatures=10000, contrastThreshold=0.02, edgeThreshold=20)
    keypoints, descriptors = sift.detectAndCompute(img, None)
    return img, keypoints, descriptors

def match_features(desc1, desc2):
    """
    Match features between two images using FLANN matcher with optimized parameters.
    """
    if desc1 is None or desc2 is None or len(desc1) < 2 or len(desc2) < 2:
        return []
        
    # FLANN parameters optimized for density
    FLANN_INDEX_KDTREE = 1
    index_params = dict(algorithm=FLANN_INDEX_KDTREE, trees=10)  # More trees for better accuracy
    search_params = dict(checks=200)  # Even more exhaustive search

    # FLANN matcher
    flann = cv2.FlannBasedMatcher(index_params, search_params)
    matches = flann.knnMatch(desc1, desc2, k=2)

    # Ratio test with slightly more permissive threshold for density
    good_matches = []
    for m, n in matches:
        # Use 0.8 instead of 0.75 to get more matches
        if m.distance < 0.8 * n.distance:
            good_matches.append(m)

    return good_matches

def triangulate_points(P1, P2, points1, points2, match_indices=None):
    """
    Triangulate 3D points from corresponding points in two views
    with improved geometric verification.
    """
    if len(points1) < 8 or len(points2) < 8:
        return np.array([]), []
        
    # Calculate fundamental matrix for geometric verification with improved parameters
    F, mask = cv2.findFundamentalMat(points1, points2, cv2.FM_RANSAC, 4.0, 0.99)
    
    if F is None or mask is None or len(mask) == 0:
        return np.array([]), []
        
    # Only keep inliers
    mask = mask.ravel().astype(bool)
    if np.sum(mask) < 8:  # Need at least 8 good points
        return np.array([]), []
        
    points1_inliers = points1[mask]
    points2_inliers = points2[mask]
    
    if match_indices is not None:
        match_indices = [idx for i, idx in enumerate(match_indices) if mask[i]]
    
    # Triangulate points with improved numerics
    points_4d_hom = cv2.triangulatePoints(P1, P2, points1_inliers.T, points2_inliers.T)
    points_3d = points_4d_hom / points_4d_hom[3]
    
    # Calculate reprojection errors
    reprojection_errors = calculate_reprojection_error(
        points_3d[:3].T, points1_inliers, points2_inliers, P1, P2, list(range(len(points1_inliers)))
    )
    
    # Filter by reprojection error with more permissive threshold for temple dataset
    good_points_mask = reprojection_errors < 10.0  # More permissive threshold for density
    
    if np.sum(good_points_mask) == 0:
        return np.array([]), []
        
    good_points_3d = points_3d[:3, good_points_mask].T
    
    if match_indices is not None:
        match_indices = [match_indices[i] for i in range(len(match_indices)) if good_points_mask[i]]
    
    return good_points_3d, match_indices

def extract_features_from_all_images(params, data_path):
    """
    Extract features from all images in the dataset.
    """
    all_features = {}
    
    for param in tqdm(params, desc="Extracting features"):
        img_name = param['img_name']
        img_path = os.path.join(data_path, img_name)
        
        if os.path.exists(img_path):
            img, keypoints, descriptors = detect_and_compute_features(img_path)
            if img is not None and len(keypoints) > 0 and descriptors is not None:
                all_features[img_name] = {
                    'img': img,
                    'keypoints': keypoints,
                    'descriptors': descriptors
                }
        else:
            print(f"Warning: Image {img_name} not found at {img_path}")
    
    print(f"Extracted features for {len(all_features)} images")
    return all_features

def angular_distance(angle1, angle2):
    """
    Calculate the angular distance between two angles in degrees.
    Takes into account the circular nature of angles.
    """
    return min(abs(angle1 - angle2), 360 - abs(angle1 - angle2))

def select_image_pairs(params, camera_angles, num_base_images=25):
    """
    Intelligently select image pairs for reconstruction using camera angles.
    Returns list of (base_idx, target_idx) pairs to process.
    """
    pairs_to_process = []
    num_images = len(params)
    
    # Choose evenly spaced base images for better coverage
    base_indices = [int(i * num_images / num_base_images) for i in range(num_base_images)]
    
    # For each base image, find good pairs based on camera angles
    for base_idx in base_indices:
        base_img_name = params[base_idx]['img_name']
        
        if base_img_name not in camera_angles:
            continue
            
        base_elevation = camera_angles[base_img_name]['elevation']
        base_azimuth = camera_angles[base_img_name]['azimuth']
        
        # Find good matching candidates
        candidates = []
        for target_idx, param in enumerate(params):
            if target_idx == base_idx:
                continue
                
            target_img_name = param['img_name']
            if target_img_name not in camera_angles:
                continue
                
            target_elevation = camera_angles[target_img_name]['elevation']
            target_azimuth = camera_angles[target_img_name]['azimuth']
            
            # Calculate angle differences
            elevation_diff = abs(base_elevation - target_elevation)
            azimuth_diff = angular_distance(base_azimuth, target_azimuth)
            
            # We want images with similar elevation but different azimuth
            # for good triangulation (15-60 degrees difference is ideal)
            if elevation_diff < 10 and 15 < azimuth_diff < 60:
                # Score based on azimuth difference (closer to 30 degrees is better)
                score = abs(azimuth_diff - 30)
                candidates.append((target_idx, score))
        
        # Sort by score and pick the best candidates
        candidates.sort(key=lambda x: x[1])
        best_matches = [idx for idx, _ in candidates[:30]]  # Take up to 30 best matches
        
        # Add the pairs
        for target_idx in best_matches:
            pairs_to_process.append((base_idx, target_idx))
    
    return pairs_to_process

def reconstruct_3d_points_from_angles(params, all_features, data_path, camera_angles):
    """
    Perform 3D reconstruction using image pairs selected based on camera angles.
    """
    all_3d_points = []
    all_point_colors = []
    
    # Select image pairs based on camera angles
    pairs_to_process = select_image_pairs(params, camera_angles, num_base_images=30)
    
    print(f"Processing {len(pairs_to_process)} image pairs selected using camera angle information")
    
    # Process each selected pair
    for base_idx, target_idx in tqdm(pairs_to_process, desc="Processing image pairs"):
        base_img_name = params[base_idx]['img_name']
        target_img_name = params[target_idx]['img_name']
        
        # Load base image for color information
        base_img_path = os.path.join(data_path, base_img_name)
        base_img = cv2.imread(base_img_path)
        
        if base_img is None or base_img_name not in all_features or target_img_name not in all_features:
            continue
            
        # Camera parameters
        base_K = params[base_idx]['K']
        base_R = params[base_idx]['R']
        base_t = params[base_idx]['t']
        
        target_K = params[target_idx]['K']
        target_R = params[target_idx]['R']
        target_t = params[target_idx]['t']
        
        # Form projection matrices
        base_P = base_K @ np.hstack((base_R, base_t.reshape(3, 1)))
        target_P = target_K @ np.hstack((target_R, target_t.reshape(3, 1)))
        
        # Match features
        good_matches = match_features(
            all_features[base_img_name]['descriptors'],
            all_features[target_img_name]['descriptors']
        )
        
        # Only proceed if we have enough matches
        if len(good_matches) < 10:
            continue
            
        # Get matched keypoints
        base_kps = all_features[base_img_name]['keypoints']
        target_kps = all_features[target_img_name]['keypoints']
        
        # Extract coordinates
        base_pts = np.float32([base_kps[m.queryIdx].pt for m in good_matches])
        target_pts = np.float32([target_kps[m.trainIdx].pt for m in good_matches])
        
        # Match indices for tracking
        match_indices = list(range(len(good_matches)))
        
        # Triangulate points with geometric verification
        points_3d, valid_match_indices = triangulate_points(base_P, target_P, base_pts, target_pts, match_indices)
        
        if len(points_3d) == 0:
            continue
            
        # Get colors from base image for valid points
        colors = []
        for idx in valid_match_indices:
            pt = base_pts[idx]
            x, y = int(pt[0]), int(pt[1])
            if 0 <= x < base_img.shape[1] and 0 <= y < base_img.shape[0]:
                color = base_img[y, x]
                colors.append(color[::-1])  # BGR to RGB
            else:
                colors.append([128, 128, 128])  # Default to gray
        
        # Add to the collection
        all_3d_points.extend(points_3d)
        all_point_colors.extend(colors)
    
    # Convert to numpy arrays
    all_3d_points = np.array(all_3d_points)
    all_point_colors = np.array(all_point_colors)
    
    return all_3d_points, all_point_colors

def camera_angle_difference(R1, R2):
    """
    Calculate the angle between two camera orientations.
    """
    # Convert rotation matrices to quaternions for better angle computation
    q1 = rotation_matrix_to_quaternion(R1)
    q2 = rotation_matrix_to_quaternion(R2)
    
    # Calculate dot product and handle numerical instability
    dot = np.clip(np.sum(q1 * q2), -1.0, 1.0)
    
    # Return the angle in radians
    return 2 * np.arccos(np.abs(dot))

def rotation_matrix_to_quaternion(R):
    """
    Convert a rotation matrix to a quaternion.
    """
    trace = np.trace(R)
    q = np.zeros(4)
    
    if trace > 0:
        s = 0.5 / np.sqrt(trace + 1.0)
        q[0] = 0.25 / s
        q[1] = (R[2, 1] - R[1, 2]) * s
        q[2] = (R[0, 2] - R[2, 0]) * s
        q[3] = (R[1, 0] - R[0, 1]) * s
    else:
        if R[0, 0] > R[1, 1] and R[0, 0] > R[2, 2]:
            s = 2.0 * np.sqrt(1.0 + R[0, 0] - R[1, 1] - R[2, 2])
            q[0] = (R[2, 1] - R[1, 2]) / s
            q[1] = 0.25 * s
            q[2] = (R[0, 1] + R[1, 0]) / s
            q[3] = (R[0, 2] + R[2, 0]) / s
        elif R[1, 1] > R[2, 2]:
            s = 2.0 * np.sqrt(1.0 + R[1, 1] - R[0, 0] - R[2, 2])
            q[0] = (R[0, 2] - R[2, 0]) / s
            q[1] = (R[0, 1] + R[1, 0]) / s
            q[2] = 0.25 * s
            q[3] = (R[1, 2] + R[2, 1]) / s
        else:
            s = 2.0 * np.sqrt(1.0 + R[2, 2] - R[0, 0] - R[1, 1])
            q[0] = (R[1, 0] - R[0, 1]) / s
            q[1] = (R[0, 2] + R[2, 0]) / s
            q[2] = (R[1, 2] + R[2, 1]) / s
            q[3] = 0.25 * s
            
    # Normalize the quaternion
    return q / np.linalg.norm(q)

def calculate_reprojection_error(points_3d, points1, points2, P1, P2, indices):
    """
    Calculate reprojection error for triangulated points.
    """
    errors = []
    
    for i, point_3d in enumerate(points_3d):
        # Get the original 2D points
        idx = indices[i]
        pt1 = points1[idx]
        pt2 = points2[idx]
        
        # Project 3D point back to 2D
        point_3d_hom = np.append(point_3d, 1)
        
        # Project to first image
        proj1 = P1 @ point_3d_hom
        proj1 = proj1[:2] / proj1[2]
        
        # Project to second image
        proj2 = P2 @ point_3d_hom
        proj2 = proj2[:2] / proj2[2]
        
        # Calculate reprojection errors
        error1 = np.linalg.norm(proj1 - pt1)
        error2 = np.linalg.norm(proj2 - pt2)
        
        # Use maximum of the two errors
        errors.append(max(error1, error2))
    
    return np.array(errors)

def filter_outliers(points_3d, point_colors, max_distance=5.0):
    """
    Filter outliers using multiple criteria but with parameters adjusted for the temple dataset.
    """
    if len(points_3d) == 0:
        return np.array([]), np.array([])
    
    # Filter by distance from the center of the object
    # For temple, we know the bounding box from README
    center = np.array([-0.003356, 0.08181, -0.005354])  # Center of the bounding box
    distances = np.linalg.norm(points_3d - center, axis=1)
    mask = distances < max_distance
    filtered_points = points_3d[mask]
    filtered_colors = point_colors[mask] if len(point_colors) > 0 else np.array([])
    
    if len(filtered_points) < 10:
        return filtered_points, filtered_colors
    
    # Create Open3D point cloud for advanced filtering
    pcd = o3d.geometry.PointCloud()
    pcd.points = o3d.utility.Vector3dVector(filtered_points)
    if len(filtered_colors) > 0:
        pcd.colors = o3d.utility.Vector3dVector(filtered_colors / 255.0)
    
    # Statistical outlier removal with gentler parameters for more density
    pcd, _ = pcd.remove_statistical_outlier(nb_neighbors=30, std_ratio=2.8)
    
    # Voxel downsampling to get more uniform point distribution
    # Using smaller voxel size for denser point cloud
    voxel_size = 0.0005  # 0.5mm voxel size for ultra-dense point cloud
    pcd = pcd.voxel_down_sample(voxel_size)
    
    filtered_points = np.asarray(pcd.points)
    filtered_colors = np.asarray(pcd.colors) * 255.0 if len(np.asarray(pcd.colors)) > 0 else np.array([])
    
    return filtered_points, filtered_colors

def visualize_point_cloud(points, colors=None):
    """
    Visualize the point cloud using Open3D.
    """
    if len(points) == 0:
        print("No points to visualize")
        return None
    
    # Create Open3D point cloud
    pcd = o3d.geometry.PointCloud()
    pcd.points = o3d.utility.Vector3dVector(points)
    
    if colors is not None and len(colors) == len(points):
        pcd.colors = o3d.utility.Vector3dVector(colors / 255.0)  # Normalize colors
    
    # Estimate normals for better visualization
    pcd.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.02, max_nn=40))
    
    # Visualize
    o3d.visualization.draw_geometries([pcd])
    
    return pcd

def create_improved_mesh(pcd, output_dir='output'):
    """
    Create an improved mesh from the point cloud using the Poisson reconstruction method.
    From the second code with better meshing strategy.
    """
    print("Creating improved mesh using Poisson reconstruction...")
    
    # Make a copy of the input point cloud
    pcd = copy.deepcopy(pcd)
    
    # 1. Preprocessing: Enhance the point cloud
    # 1.1 Ensure normals are properly estimated and oriented
    pcd.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.01, max_nn=50))
    pcd.orient_normals_consistent_tangent_plane(k=100)
    
    # 1.2 Remove outliers one more time with stricter parameters
    pcd, _ = pcd.remove_statistical_outlier(nb_neighbors=50, std_ratio=2.0)
    
    # 1.3 Apply smoothing to reduce noise while preserving features
    pcd.normals = o3d.utility.Vector3dVector(np.asarray(pcd.normals) * 0.5)  # Reduce normal strength
    
    # 2. Create mesh using Poisson reconstruction
    print("Performing Poisson reconstruction...")
    # Create a copy with stronger normal consistency for Poisson
    pcd_poisson = copy.deepcopy(pcd)
    pcd_poisson.estimate_normals(search_param=o3d.geometry.KDTreeSearchParamHybrid(radius=0.01, max_nn=30))
    pcd_poisson.orient_normals_consistent_tangent_plane(100)
    
    # Use a higher depth for more detail, but carefully tune scale
    mesh_poisson, densities = o3d.geometry.TriangleMesh.create_from_point_cloud_poisson(
        pcd_poisson, depth=9, width=0, scale=1.1, linear_fit=False)
    
    # More aggressive density filtering to remove artifacts
    vertices_to_remove = densities < np.quantile(densities, 0.1)  # Remove more low-density vertices
    mesh_poisson.remove_vertices_by_mask(vertices_to_remove)
    
    # Clean up the Poisson mesh
    mesh_poisson.remove_degenerate_triangles()
    mesh_poisson.remove_duplicated_triangles()
    mesh_poisson.remove_duplicated_vertices()
    mesh_poisson.remove_non_manifold_edges()
    
    # 3. Post-processing
    final_mesh = post_process_mesh(mesh_poisson)
    
    # 4. Optional - Transfer colors from point cloud to mesh
    if pcd.has_colors():
        # Create a KDTree for the point cloud
        pcd_tree = o3d.geometry.KDTreeFlann(pcd)
        
        # For each vertex in the mesh, find closest point in the point cloud
        vertices = np.asarray(final_mesh.vertices)
        vertex_colors = []
        
        for vertex in vertices:
            # Find the nearest neighbor in the point cloud
            k, idx, _ = pcd_tree.search_knn_vector_3d(vertex, 1)
            # Get the color of the nearest point
            nearest_color = np.asarray(pcd.colors)[idx[0]]
            vertex_colors.append(nearest_color)
        
        # Set the vertex colors in the mesh
        final_mesh.vertex_colors = o3d.utility.Vector3dVector(np.array(vertex_colors))
    
    # 5. Save the final mesh
    os.makedirs(output_dir, exist_ok=True)
    output_path = os.path.join(output_dir, 'temple_mesh_improved.ply')
    o3d.io.write_triangle_mesh(output_path, final_mesh)
    print(f"Improved mesh saved to {output_path}")
    
    return final_mesh

def post_process_mesh(mesh):
    """
    Apply post-processing to a mesh to improve quality.
    From second code with better mesh post-processing.
    """
    # Mesh filtering to smooth while preserving features
    mesh = mesh.filter_smooth_simple(number_of_iterations=5)
    mesh.compute_vertex_normals()
    
    # Identify non-manifold edges which often indicate holes
    mesh.compute_adjacency_list()
    edges = set()
    
    # Find boundary edges (edges that belong to only one triangle)
    # This is manual implementation of boundary detection
    triangles = np.asarray(mesh.triangles)
    for tri in triangles:
        for i in range(3):
            edge = (min(tri[i], tri[(i+1)%3]), max(tri[i], tri[(i+1)%3]))
            if edge in edges:
                edges.remove(edge)
            else:
                edges.add(edge)
    
    print(f"Identified {len(edges)} boundary edges that could indicate holes")
    
    # Final cleanup pass
    mesh.remove_degenerate_triangles()
    mesh.remove_duplicated_triangles()
    mesh.remove_duplicated_vertices()
    mesh.remove_non_manifold_edges()
    
    return mesh

def main_dense_reconstruction_pipeline(params, data_path, angle_file_path):
    """
    Main pipeline for dense 3D reconstruction using camera angle information.
    Integrated with improved meshing strategy.
    """
    # 1. Load camera angles
    camera_angles = load_camera_angles(angle_file_path)
    print(f"Loaded camera angles for {len(camera_angles)} images")
    
    # 2. Extract features from all images
    all_features = extract_features_from_all_images(params, data_path)
    
    # 3. Reconstruct 3D points using camera angle information
    all_3d_points, all_point_colors = reconstruct_3d_points_from_angles(params, all_features, data_path, camera_angles)
    
    print(f"Initial reconstruction has {len(all_3d_points)} points")
    
    # Save the raw point cloud
    if len(all_3d_points) > 0:
        raw_pcd = o3d.geometry.PointCloud()
        raw_pcd.points = o3d.utility.Vector3dVector(all_3d_points)
        if len(all_point_colors) > 0:
            raw_pcd.colors = o3d.utility.Vector3dVector(all_point_colors / 255.0)
        
        output_dir = 'output'
        os.makedirs(output_dir, exist_ok=True)
        raw_output_path = os.path.join(output_dir, 'raw_dense_reconstruction.ply')
        o3d.io.write_point_cloud(raw_output_path, raw_pcd)
        print(f"Raw dense point cloud saved to {raw_output_path}")
    
    # 4. Filter outliers
    filtered_points, filtered_colors = filter_outliers(all_3d_points, all_point_colors)
    
    print(f"After filtering: {len(filtered_points)} points")
    
    # 5. Visualize and save results
    if len(filtered_points) > 0:
        pcd = visualize_point_cloud(filtered_points, filtered_colors)
        
        # Save the filtered point cloud
        output_dir = 'output'
        os.makedirs(output_dir, exist_ok=True)
        output_path = os.path.join(output_dir, 'ultra_dense_reconstruction.ply')
        
        o3d.io.write_point_cloud(output_path, pcd)
        print(f"Ultra dense point cloud saved to {output_path}")
        
        # 6. Apply improved meshing (from second code)
        print("\n--- Applying improved meshing strategy ---")
        final_mesh = create_improved_mesh(pcd)
        
        # Visualize the final mesh
        print("\nShowing final improved mesh...")
        o3d.visualization.draw_geometries([final_mesh], mesh_show_back_face=True)
        
        return pcd, final_mesh
    else:
        print("No points to visualize after filtering")
        return None, None

# usage:
# angle_file_path = "temple/temple_ang.txt"
# pcd, final_mesh = main_dense_reconstruction_pipeline(params, data_path, angle_file_path)

In [10]:
angle_file_path = "temple/temple_ang.txt"
pcd, final_mesh = main_dense_reconstruction_pipeline(params, data_path, angle_file_path)

Loaded camera angles for 312 images


Extracting features: 100%|██████████| 312/312 [00:29<00:00, 10.41it/s]


Extracted features for 312 images
Processing 450 image pairs selected using camera angle information


Processing image pairs: 100%|██████████| 450/450 [01:20<00:00,  5.62it/s]


Initial reconstruction has 87592 points
Raw dense point cloud saved to output\raw_dense_reconstruction.ply
After filtering: 30762 points
[Open3D WARNING] GLFW Error: WGL: Failed to make context current: The requested transformation operation is not supported. 
[Open3D WARNING] GLFW Error: WGL: Failed to make context current: The handle is invalid. 
[Open3D WARNING] GLFW Error: WGL: Failed to make context current: The requested transformation operation is not supported. 
Ultra dense point cloud saved to output\ultra_dense_reconstruction.ply

--- Applying improved meshing strategy ---
Creating improved mesh using Poisson reconstruction...
Performing Poisson reconstruction...
Identified 3134 boundary edges that could indicate holes
Improved mesh saved to output\temple_mesh_improved.ply

Showing final improved mesh...
[Open3D WARNING] GLFW Error: WGL: Failed to make context current: The requested transformation operation is not supported. 
[Open3D WARNING] GLFW Error: WGL: Failed to make c